![CNRS](https://anf-tdm-2022.sciencesconf.org/data/header/LOGO_CNRS_CMJN_150x150.png)


# Tutoriel - ANF TDM 2022 Python Geoparsing 

Supports pour l'atelier [Librairies Python et Services Web pour la reconnaissance d’entités nommées et la résolution de toponymes](https://anf-tdm-2022.sciencesconf.org/resource/page/id/11) de la formation CNRS [ANF TDM 2022](https://anf-tdm-2022.sciencesconf.org).

**Animateurs**: [Ludovic Moncla](https://ludovicmoncla.github.io) (INSA Lyon) et [Alice Brenon](https://perso.liris.cnrs.fr/abrenon/) (CNRS / INSA Lyon)

## 1. En bref


Dans ce tutoriel, nous allons apprendre plusieurs choses :

- Charger des jeux de données :
  - à partir de fichiers txt importés depuis le disque dur ;
  - à partir de la librairie Python [Perdido](https://github.com/ludovicmoncla/perdido) dans un [Pandas dataframe](https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.html) (articles encyclopédiques et descriptions de randonnées).
- Manipuler et interroger un dataframe
- Utiliser les librairies [Stanza](https://stanfordnlp.github.io/stanza/index.html), [spaCy](https://spacy.io) et [Perdido](https://github.com/ludovicmoncla/perdido) pour la reconnaissance d'entités nommées
  - afficher les entités nommées annotées ;
  - comparer les résultats de `Stanza`, `spaCy` et `Perdido` ;
  - discuter les limites des 3 outils pour la tâche de NER.
- Utiliser la librarie `Perdido` pour le geoparsing :
  - cartographier les lieux geocodés ;
  - illustrer la problématique de désambiguïsation des toponymes.

## 2. Introduction

## 3. Configurer l'environnement

### 3.1 Installer les librairies Python

* Si vous avez configuré votre environnement Conda en utilisant le fichier `requirements.txt`, vous pouvez sauter cette étape et aller à la section `3.2 Importer les librairies`.
* Si vous avez configuré votre environnement Conda en utilisant le fichier `environment.yml` ou si vous utilisez un environnement Google Colab / Binder, vous devez installer `perdido` en utilisant `pip` :

In [ ]:
!pip install perdido

* Si vous avez déjà configuré votre environnement conda, soit avec conda, soit avec pip (voir le fichier readme), vous pouvez ignorer la cellule suivante.
* Si vous exécutez ce notebook depuis Google Colab / Binder, vous devez exécuter la cellule suivante :


In [ ]:
!pip install stanza

### 3.2 Importer les librairies


Tout d'abord, nous allons charger certaines bibliothèques spécifiques de `Perdido` que nous utiliserons dans ce notebook. Ensuite, nous importons quelques outils qui nous aideront à analyser et à visualiser le texte.

In [1]:
import warnings
warnings.filterwarnings('ignore')

from perdido.geoparser import Geoparser
from perdido.geocoder import Geocoder

from perdido.datasets import load_edda_artfl, load_edda_perdido, load_choucas_perdido

from spacy import displacy

## 4. Chargement et exploration des données

### 4.1 Chargement d'un document texte à partir d'un fichier


In [2]:
filepath = 'data/volume01-4083.txt'

In [3]:
with open(filepath) as f:
    content = f.read()

* Afficher le contenu du fichier

In [4]:
print(content)

* ARQUES, (Géog.) petite ville de France, en Normandie, au pays de Caux, sur la petite riviere d'Arques. Long. 18. 50. lat. 49. 54.


### 4.2 Chargement d'un jeu de données à partir de la librairie Perdido

Perdido embarque deux jeux de données : 
 1. articles encyclopédiques (volume 7 de l'Encyclopédie de Diderot et d'Alembert (1751-1772)), fournit par l'[ARTFL](https://encyclopedie.uchicago.edu) dans le cadre du projet [GEODE](https://geode-project.github.io) ;
 2. descriptions de randonnées (chaque description est associée à sa trace GPS. Elles proviennent du site [www.visorando.fr](https://www.visorando.com) et ont été collectées dans le cadre du projet [ANR CHOUCAS](http://choucas.ign.fr).

 Dans un premier temps nous allons nous intéresser au jeu de données des articles encyclopédiques. Ce jeu de données est présent dans la librairie en deux versions, une version "brute" (articles fournis par l'ARTFL) au format dataframe et une version déjà annotée par Perdido (format PerdidoCollection). Nous allons charger la version brute et voir comment manipuler un dataframe.

* Charger le jeu de données :

In [5]:
dataset_artfl = load_edda_artfl()
data_artfl = dataset_artfl['data']

* Afficher les informations sur le jeu de données :

In [6]:
data_artfl.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3385 entries, 0 to 3384
Data columns (total 7 columns):
 #   Column     Non-Null Count  Dtype 
---  ------     --------------  ----- 
 0   filename   3385 non-null   object
 1   volume     3385 non-null   int64 
 2   number     3385 non-null   int64 
 3   head       3384 non-null   object
 4   normClass  3384 non-null   object
 5   author     3384 non-null   object
 6   text       3385 non-null   object
dtypes: int64(2), object(5)
memory usage: 185.2+ KB


On remarque que certaines colonnes ont une donnée manquante (3384 lignes non nulles contre 3385 lignes au total). Pour la suite des opérations que nous allons réaliser il est nécessaire de supprimer les lignes incomplètes.

* Supprimer la ligne incomplète :

In [7]:
data_artfl.dropna(inplace=True)     # data_artfl = data_artfl.dropna()


* Vérifier le résultat :

In [8]:
data_artfl.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 3384 entries, 0 to 3384
Data columns (total 7 columns):
 #   Column     Non-Null Count  Dtype 
---  ------     --------------  ----- 
 0   filename   3384 non-null   object
 1   volume     3384 non-null   int64 
 2   number     3384 non-null   int64 
 3   head       3384 non-null   object
 4   normClass  3384 non-null   object
 5   author     3384 non-null   object
 6   text       3384 non-null   object
dtypes: int64(2), object(5)
memory usage: 211.5+ KB


* Afficher la liste des premiers articles :

In [9]:
data_artfl.head()

filename  volume  number              head             normClass  \
0     volume07-1.tei       7       1        Title Page          unclassified   
1    volume07-10.tei       7      10  FOESNE ou FOUANE        Marine | Pêche   
2   volume07-100.tei       7     100   Fond de la hune          unclassified   
3  volume07-1000.tei       7    1000          Fronteau  Bourrelier | Sellier   
4  volume07-1001.tei       7    1001         FRONTIERE            Géographie   

     author                                               text  
0  unsigned  ENCYCLOPÉDIE, ou DICTIONNAIRE RAISONNÉ DES SCI...  
1    Bellin  FOESNE ou FOUANE, sub. s. (Marine & Pêche.) c'...  
2    Bellin  Fond de la hune ; ce sont les planches qu on p...  
3   Diderot  * Fronteau, terme de Sellier-Bourrelier ; c'es...  
4   Diderot  * FRONTIERE, s. f. (Géog.) se dit des limites,...

### 4.3 Manipulation d'un dataframe

Nous avons maintenant accès à tous les attributs et méthodes de l'objet [dataframe](https://pandas.pydata.org/pandas-docs/stable/reference/api/pandas.DataFrame.html). Par exemple, nous pouvons facilement connaître le nombre de lignes dans notre dataframe qui correspond au nombre d'articles dans notre corpus :

In [10]:
n = data_artfl.shape[0]
print('Il y a ' + str(n) + ' articles dans le jeu de données.')

Il y a 3384 articles dans le jeu de données.


#### 4.3.1 Recherche par métadonnées


Maintenant que les données sont chargées dans un dataframe, nous pouvons sélectionner des groupes d'articles sur la base de leurs métadonnées.

Pour cela on utilise la méthode [loc()](https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.loc.html).



* Selectionner la ligne du dataframe qui correspond à l'article 'FRONTIGNAN' :

In [11]:
frontignan = data_artfl.loc[data_artfl['head'] == 'FRONTIGNAN']
frontignan 

filename  volume  number        head   normClass    author  \
5  volume07-1002.tei       7    1002  FRONTIGNAN  Géographie  Jaucourt   

                                                text  
5  FRONTIGNAN, (Géog.) petite ville de France. au...

* Récupérer les valeurs des attributs (colonnes) :

In [18]:
print('filename :', frontignan.filename.item())   # similaire à frontignan['normClass'].item()

print('text :', frontignan.text.item())


filename : volume07-1002.tei
text : FRONTIGNAN, (Géog.) petite ville de France. au Bas-Languedoc, connue par ses excellens vins muscats, & ses raisins de caisse qu'on appelle passerilles. Quelques savans croyent, sans en donner de preuves, que cette ville est le forum Domitii des Romains. Elle est située sur l'étang de Maguelone, à six lieues N. E. d'Agde, & cinq S. O. de Montpellier. Long. 15d. 24'. lat. 43d. 28'. (D. J.)


Nous pouvons également filtrer les données sur la base de l'auteur.

* Extraire les articles rédigés par Jaucourt :

In [19]:
req = 'Jaucourt'
d_Jaucourt = data_artfl.loc[data_artfl['author'] == req]

n = d_Jaucourt.shape[0]
print(str(n) + ' articles ont été rédigés par '+ req)

698 articles ont été rédigés par Jaucourt


In [20]:
d_Jaucourt.head()

filename  volume  number                           head  \
5   volume07-1002.tei       7    1002                     FRONTIGNAN   
29  volume07-1024.tei       7    1024               FROWARD, le cap.   
32  volume07-1027.tei       7    1027                      FRUGALITÉ   
37  volume07-1031.tei       7    1031                  Fruit verreux   
38  volume07-1032.tei       7    1032  Fruit, (art de conserver le)    

             normClass    author  \
5           Géographie  Jaucourt   
29          Géographie  Jaucourt   
32              Morale  Jaucourt   
37  Histoire naturelle  Jaucourt   
38   Economie rustique  Jaucourt   

                                                 text  
5   FRONTIGNAN, (Géog.) petite ville de France. au...  
29  FROWARD, le cap. (Géog.) & par les François le...  
32  FRUGALITÉ, (Morale.) simplicité de moeurs & de...  
37  Fruit verreux, (Hist. nat.) c'est le nom qu'on...  
38  Fruit, (art de conserver le) Economie rustiq. ...

Autre exemple, nous pouvons filtrer les articles en fonction de leur classification dans l'*Encyclopédie*. 
Pour cela nous utiliserons le champ `normclass`, qui indique la classifications retenue (et normalisée) par l'ARTFL. 

Par exemple pour la classe 'Géographie', nous pouvons faire la requête suivante (le résultat est stocké dans un nouveau cadre de données `df_geo` : 

In [21]:
req = 'Géographie'
d_geo = data_artfl[data_artfl['normClass'].str.contains(req, case=False)]

n = d_geo.shape[0]
print(str(n) + ' articles sont classés en '+ req)

496 articles sont classés en Géographie


On peut également regrouper les données selon un ou plusieurs attributs (colonnes) et compter le nombre de données de chaque groupe avec les méthodes [groupby()](https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.groupby.html) et [count()](https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.count.html).

* Afficher le nombre d'articles classés en Géographie par auteur :

In [22]:
d_geo.groupby(['author'])["filename"].count()

author
Desmarest                            1
Diderot                              1
Jaucourt                           476
La Condamine                         1
Mallet                               1
Robert de Vaugondy                   2
Robert de Vaugondy & d'Alembert      1
unsigned                            13
Name: filename, dtype: int64

Dans cette partie nous avons vu brievement comment manipuler un dataframe pour selectionner certaines données en filtrant selon certaines métadonnées ou par une recheche par mot clés. Ces opérations sont utiles mais un peu limitées, nous allons voir dans la suite de ce notebook comment enrichir les métadonnées et en particulier comment annoter les entités nommées présents dans les textes.

## 5. Reconnaissance d'Entités Nommées (NER)

La reconnaissance d'entités nommées, *Named Entity Recognition* (NER) en anglais, est une tâche très importante et incontournable en traitement automatique des langues (TAL) et en compréhension du langage naturel (NLU en anglais). 
Cette tâche consiste à rechercher des objets textuels (un mot, ou un groupe de mots, souvent associés aux noms propres) catégorisables dans des classes telles que noms de personnes, noms d'organisations ou d'entreprises, noms de lieux, quantités, distances, valeurs, dates, etc.

Dans cet atelier nous allons expérimenter et comparer trois outils de NER. 

1. [Stanza](https://stanfordnlp.github.io/stanza/index.html)
2. [spaCy](https://spacy.io)
3. [Perdido](https://github.com/ludovicmoncla/perdido)

### 5.1 Stanza NER

`Stanza` est une librairie Python de traitement du langage naturel. Elle contient des outils, qui peuvent être utilisés dans une chaîne de traitement, pour convertir du texte en listes de phrases et de mots, pour générer les formes de base de ces mots, leurs parties du discours et leurs caractéristiques morphologiques, pour produire une analyse syntaxique de dépendance, et pour reconnaître les entités nommées. 

`Stanza` se base sur des modèles entrainés par des réseaux de neurones à partir de la bibliothèque [PyTorch](https://pytorch.org) et permet de traiter plus de 70 langues.

Dans cette partie nous allons voir comment utiliser `Stanza` pour la reconnaissance d'entités nommées à partir de textes en français.


* Importer la librairie `Stanza` et télécharger le modèle pré-entrainé pour le français : 

In [23]:
import stanza

stanza.download('fr')

2022-09-16 09:16:43 INFO: Downloading default packages for language: fr (French)...
2022-09-16 09:16:44 INFO: File exists: /Users/lmoncla/stanza_resources/fr/default.zip
2022-09-16 09:16:47 INFO: Finished downloading models and saved to /Users/lmoncla/stanza_resources.


* Instancier et paramétrer la chaîne de traitement :

In [24]:
stanza_parser = stanza.Pipeline(lang='fr', processors='tokenize,ner')

2022-09-16 09:16:56 WARNING: Language fr package default expects mwt, which has been added
2022-09-16 09:16:57 INFO: Loading these models for language: fr (French):
| Processor | Package |
-----------------------
| tokenize  | gsd     |
| mwt       | gsd     |
| ner       | wikiner |

2022-09-16 09:16:57 INFO: Use device: cpu
2022-09-16 09:16:57 INFO: Loading: tokenize
2022-09-16 09:16:57 INFO: Loading: mwt
2022-09-16 09:16:57 INFO: Loading: ner
2022-09-16 09:16:58 INFO: Done loading processors!


* On utilise la variable `content` qui contient le texte chargé précédemment à partir du fichier

In [27]:
print(content)

* ARQUES, (Géog.) petite ville de France, en Normandie, au pays de Caux, sur la petite riviere d'Arques. Long. 18. 50. lat. 49. 54.


* Executer la reconnaissance d'entités nommées :

In [25]:
doc = stanza_parser(content)

* Afficher la liste des entités nommées repérées :

In [28]:
for ent in doc.ents:
    print(ent.text, ent.type)

ARQUES LOC
(Géog LOC
France LOC
Normandie LOC
pays de Caux LOC
Arques LOC


### 5.2 SpaCy NER


`spaCy` est également une librairie Python de traitement du langage naturel. 
Elle se compose de modèles pré-entrainés et supporte actuellement la tokenisation et l'entrainement pour plus de 60 langues. Elle est doté de modèles de réseaux neuronaux pour le balisage, l'analyse syntaxique, la reconnaissance d'entités nommées, la classification de textes, l'apprentissage multi-tâches avec des transformateurs pré-entraînés comme BERT, ainsi qu'un système d'entraînement prêt pour la production et un déploiement simple des modèles. `spaCy` est un logiciel commercial, publié en open-source sous la licence MIT.

Dans cette partie nous allons voir comment utiliser `spaCy` pour la reconnaissance d'entités nommées toujours à partir de notre exemple en français.

* Installer le modèle français pré-entrainé de `spaCy` :

In [29]:
!python -m spacy download fr_core_news_sm

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 16.3/16.3 MB 10.7 MB/s eta 0:00:0000:0100:01
✔ Download and installation successful
You can now load the package via spacy.load('fr_core_news_sm')


* Importer la librarie `spaCy` :

In [30]:
import spacy

* Charger le modèle français pré-entrainé de `spaCy`

In [31]:
spacy_parser = spacy.load('fr_core_news_sm')

* Executer la reconnaissance d'entités nommées :

In [32]:
doc = spacy_parser(content)

* Afficher la liste des entités nommées repérées :

In [33]:
for ent in doc.ents:
    print(ent.text, ent.label_)

Géog MISC
de France LOC
Normandie LOC
pays de Caux LOC
Arques LOC


* Afficher de manière graphique les entités nommées avec `displaCy` :

In [34]:
displacy.render(doc, style="ent", jupyter=True) 

### 5.3 Perdido Geoparser

* Instancier et paramétrer la chaîne de traitement :

In [35]:
geoparser = Geoparser(version="Encyclopedie")

* Executer la reconnaissance d'entités nommées :

In [41]:
doc = geoparser(content)

* Afficher la liste des entités nommées repérées :

In [42]:
for ent in doc.named_entities:
    print(ent.text, ent.tag)

ARQUES place
France place
Normandie place
Caux place
Arques place
Long . 18 . 50 . lat . 49 . 54 . latlong


* Afficher de manière graphique les entités nommées avec `displaCy` :

In [43]:
displacy.render(doc.to_spacy_doc(), style="ent", jupyter=True)

* Afficher de manière graphique les entités nommées étendues avec `displaCy` :

In [44]:
displacy.render(doc.to_spacy_doc(), style="span", jupyter=True)

### 5.4 Expérimentations et comparaison

## 6. Geoparsing / Geocoding

En complément de la tâche de reconnaissance des entités nommées la librairie `Perdido` propose également celle de résolution des toponymes, on parle alors de *Geoparsing*. Cette tâche consiste a associer à un nom de lieu des coordonnées géographiques non ambigus. De manière classique elle s'appuie sur le repérage des entités spatiales identifées lors de la reconnaissance des entités nommées et fait appel à des ressources externes de type *gazetier* (ou dictionnaires topographique) pour localiser les lieux.

### 6.1 Perdido Geoparser

* On re-execute Perdido sur l'exemple de l'article `ARQUES`

In [55]:
content = "* ARQUES, (Géog.) petite ville de France, en Normandie, au pays de Caux, sur la petite riviere d'Arques. Long. 18. 50. lat. 49. 54."
doc = geoparser(content)

* En plus de pouvoir afficher la liste des entités nommées comme nous l'avons fait précédemmment, nous pouvons directement afficher la carte des lieux localisés

In [56]:
displacy.render(doc.to_spacy_doc(), style="ent", jupyter=True)

In [57]:
# afficher la carte des lieux localisés
doc.get_folium_map()

Par défaut, lors de l'instanciation du `Geoparser()`, seul [OpenStreetMap](https://www.openstreetmap.org/) est utilisé pour le geocoding et au maximum un résultat est retourné pour chaque lieu (nous verrons dans la suite comment paramétrer le geocoding).

On a déjà ici un aperçu de la difficulté de la tâche de résolution des toponymes. En effet, un grand nombre d'ambiguïtés existent tels que plusieurs lieux ayant le même nom, plusieurs noms pour un même lieu ou encore le fait qu'un lieu ne soit pas référencé dans les ressources que l'on interroge.

### 6.2 Perdido Geocoder

En complément du `Geoparser` qui prend en paramètre un texte et qui fait la reconnaissance d'entités nommées en amont de l'étape de geocoding, `Perdido`propose également une fonction de geocoding disctincte prenant en paramètre directement un nom de lieu (ou une liste de noms de lieux).

In [61]:
geocoder = Geocoder()
doc = geocoder(['Arques', 'France', 'Normandie', 'Caux'])

# afficher la carte des lieux localisés
doc.get_folium_map()

### 6.2 Résolution de toponymes / désambiguïsation


#### 6.2.1 Exemple : Arques

* Cherchons à localiser la ville `Arques`


In [62]:
geocoder = Geocoder()
doc = geocoder('Arques')
doc.get_folium_map()

On remarque que par défaut, la localisation retournée pour le nom de lieu `Arques` n'est pas celle que l'on recherche. En effet, le texte indique qu'il s'agit d'une ville de Normandie hors ici la localisation proposée est située dans le Pas-de-Calais !

Changeons les paramètres du `Geocoder` (ces paramètres sont similaires pour le `Geoparser`) pour essayer de retrouver la bonne localisation.

* Augmenter le nombre de résultats retournés par les gazetiers interrogés

In [67]:
geocoder = Geocoder(max_rows=10)
doc = geocoder('Arques')
doc.get_folium_map()

On observe parmi les 10 localisations retournées par OpenStreetMap (gazetier par défaut) qu'aucune ne se situe en Normandie.

* Remplacer OpenStreetMap par l'IGN

In [68]:
geocoder = Geocoder(sources=['ign'])
doc = geocoder('Arques')
doc.get_folium_map()

On observe que le premier résultat retourné par l'IGN ne se situe ni en Normandie (comme attendu), ni dans le Pas-de-Calais comme le premier résultat retourné par OpenStreetMap.

* Augmenter le nombre de résultats retournés par l'IGN

In [69]:
geocoder = Geocoder(sources=['ign'], max_rows=10)
doc = geocoder('Arques')
doc.get_folium_map()

Cette fois-ci on retrouve bien une localisation en Normandie au sud de Dieppe avec pour nom `Arques-la-Bataille'. On peut faire l'hypotèse que le nom a évolué car cette localisation se situe bien dans le Pays de Caux (voir illustration ci-dessous, source [Wikipedia](https://fr.wikipedia.org/wiki/Pays_de_Caux)) comme l'indique le texte de l'article.

![Pays de Caux](https://upload.wikimedia.org/wikipedia/commons/thumb/4/4e/Carte_pays_Caux1.png/497px-Carte_pays_Caux1.png)

Il reste néanmoins le problème de retrouver cette localisation de manière automatique. 
Plusieurs approches existent dans la littérature mais ne sont pas encore implémentées dans `Perdido`.

Cet exemple illustre bien la difficulté de la problématique de désambiguïsation des toponymes avec notamment la gestion des natures de lieux différentes (pays, régions, communes, lieux-dits, lac, rivières, etc.) associés à un même nom, l'homonymie, la non exaustivité des ressources, l'évolution des noms au cours du temps ou encore les erreurs d'orthographe.

* Afficher la carte obtenue après le geoparsing avec l'IGN et 10 résultats max par nom de lieu

In [79]:
geoparser = Geoparser(sources=['ign'], max_rows=10)
doc = geoparser(content)
doc.get_folium_map()


### 6.3 Le cas des descriptions de randonnées

Prenons maintenant l'exemple du geoparsing de descriptions de randonnées. Certaines solutions de désambiguisation ont pu être développées et intégrées au sein de la librairie `Perdido` (d'autres sont en cours d'intégration). Les solutions décrites dans la suite de cette partie ont été développées dans le cadre des projets [Perdido](http://erig.univ-pau.fr/PERDIDO/) (2012-2015) et [ANR CHOUCAS](http://choucas.ign.fr) (2017-2022). 

> Ludovic Moncla, Walter Renteria-Agualimpia, Javier Nogueras-Iso and Mauro Gaio (2014). "Geocoding for texts with fine-grain toponyms: an experiment on a geoparsed hiking descriptions corpus". In Proceedings of the 22nd ACM SIGSPATIAL International Conference on Advances in Geographic Information Systems, pp 183-192.

> Mauro Gaio and Ludovic Moncla (2019). “Geoparsing and geocoding places in a dynamic space context.“ In The Semantics of Dynamic Space in French: Descriptive, experimental and formal studies on motion expression, 66, 353.


* Charger le jeu de données CHOUCAS de descriptions de randonnées fourni par `Perdido`

In [81]:
dataset_choucas = load_choucas_perdido()
data_choucas = dataset_choucas['data']


data_choucas.to_dataframe().head()

name  \
0                       Chalets de la Fullie   
1  Traversée cabane de Pravouta  à la Plagne   
2  Refuge Entre Le Lac - Refuge de la Leisse   
3                           Le lac du Retour   
4        Traversée Alpette - Dent de Crolles   

                                                text  \
0  \n\nBoucle des chalets de la Fullie au départ ...   
1  \n\nPartir de la cabane de Pravouta juste de l...   
2  \n\nDépart du refuge d'Entre le Lac près du la...   
3  \n\nDu parking de Pierre Giret, suivre la rout...   
4                                                 \n   

                                            geometry  #_places  #_person  \
0  (LINESTRING (6.11174 45.616041, 6.11174 45.616...        17         0   
1  (LINESTRING (5.832543 45.315222, 5.832444 45.3...        23         2   
2  (LINESTRING (6.839184 45.480323, 6.83987 45.47...        22         0   
3  (LINESTRING (6.917631 45.619278, 6.917527 45.6...         6         1   
4  (LINESTRING (5.907402 45.440585, 5.907439 45.4...         0         0   

   #_event  #_date  #_misc  #_locations  
0        0       0       0           17  
1        0       0       0           23  
2        0       0       0           22  
3        0       0       0            6  
4        0       0       0            0

In [82]:
len(data_choucas)

30

* Sélectionner une randonnée (parmi les 30)

In [108]:
id_rando = 2
doc = data_choucas[id_rando]

In [109]:
doc.text

"\n\nDépart du refuge d'Entre le Lac près du lac de la Plagne.\nDu refuge Entre le Lac, un sentier remonte les pentes herbeuses et permet de rejoindre le GR5 un peu avant le chalet de la Grassaz (chalet du berger 2335m). Toujours en direction du sud, on remonte le vallon en longeant le ruisseau. On parvient ainsi à l'extrémité ouest du lac de Grattaleu; un peu plus haut, on atteint le refuge du col du Palet (2550m). On admire la beauté de la vallée et le sommet de Bellecote recouvert de glaciers. Le GR descend vers l'Est; le sentier serpente entre des entonnoirs créés dans le gypse par dissolution. Le GR passe sous un 1er télésiège, celui de Grattaleu, et près de l'arrivée d'un second, le Tichot. Au chalet de Lognan (croix) prendre à droite un sentier qui descend à Val Claret (2107m) (station de ski). Poursuivre jusqu'au chalet de la Leisse. Le GR55 s'élève vers le vallon du paquis. On passe en contrebas du chalet du Prariond; un peu plus loin on arrive à la bifurcation du col de Fress

In [110]:
displacy.render(doc.to_spacy_doc(), style="ent", jupyter=True) 

In [126]:
doc.get_folium_map()

On observe ici le résultat déjà pré-traité par `Perdido`. Nous allons maintenant illustrer le processus de désambiguïsation.

On recommence le processus de geoparsing en entier à partir du texte de la randonnées choisie.

In [128]:
geoparser = Geoparser()
doc_geoparsed = geoparser(doc.text)

In [129]:
doc_geoparsed.get_folium_map()

On voit clairement la différence par rapport au résultat précédent. Nous allons alors essayer de retrouver le même résultat en déroulant les différentes étapes pour désambiguïser avec `Perdido`.

Pour gagner un peu de temps lors des prochaines executions nous allons faire directement appel à la fonction de geocoding à partir de la liste des noms de lieux.

* Récuperer la liste des noms de lieux (sans doublon)

In [130]:
places_list = list(set([ent.text for ent in doc_geoparsed.ne_place]))
print(places_list)

['Prariond', 'col', 'Fresse', 'berger', 'Leisse', 'Grassaz', 'Tichot', 'Nettes', 'Grande', 'GR', 'Grattaleu', 'Lognan', 'Plagne', 'Claret', 'Bellecote', 'Palet', 'paquis']


#### 6.3.1 Ajout d'un filtre "code pays"


In [137]:
# instancier le geocoder avec le code pays
geocoder = Geocoder(country_code = 'fr')
doc_geocoded = geocoder(places_list)

# ajouter la trace GPS 
doc_geocoded.geometry_layer = doc.geometry_layer

doc_geocoded.get_folium_map()

#### 6.3.2 Ajout d'un filtre "bounding box"

In [140]:
bbox = [5.62216508714297, 45.051683489057, 7.18563279407213, 45.9384576816403] # zone d'intervention du PGHM Isère

# instancier le geocoder avec le code pays et une bounding box
geocoder = Geocoder(country_code = 'fr', bbox = bbox)
doc_geocoded = geocoder(places_list)

# ajouter la trace GPS 
doc_geocoded.geometry_layer = doc.geometry_layer

# affiche la carte
doc_geocoded.get_folium_map()

#### 6.3.3 Clustering par densité spatiale

In [141]:
# appliquer la désambiguïsation 
doc_geocoded.cluster_disambiguation()
doc_geocoded.get_folium_map()

Désambiguisation basé sur la proximité géographique

Clustering avec la méthode DBSCAN implémenté dans la librairie [Scikit-Learn](https://scikit-learn.org/stable/modules/generated/sklearn.cluster.DBSCAN.html). Cette stratégie est adaptée pour une description d'itinéraire où les différents lieux cités doivent être localisés à proximité les uns des autres.

Utilisation du contexte (autres entités nommées repérées dans le texte, relations spatiales, etc...). Développées dans le cadre du projet [Perdido]() (add ref 2014 et 2016) mais pas encore intégré à la librairie Python Perdido. Cette librairie est toujours en cours de développement et d'amélioration. Vos remarques et retours seront les bienvenues.